In [1]:
import osmnx as ox, networkx as nx, geopandas as gpd, matplotlib.pyplot as plt
from shapely.geometry import Point, Polygon, LineString
from descartes import PolygonPatch
import requests
import matplotlib.cm as cm
import matplotlib.colors as colors
import pandas as pd
import numpy as np
import folium
from pyproj import Proj, transform
ox.config(use_cache=True, log_console=True)

C:\Users\ilese\AppData\Local\Temp\ipykernel_4460\1303955437.py:11: FutureWarning: The `utils.config` function is deprecated and will be removed in the v2.0.0 release. Instead, use the `settings` module directly to configure a global setting's value. For example, `ox.settings.log_console=True`. See the OSMnx v2 migration guide: https://github.com/gboeing/osmnx/issues/1123
  ox.config(use_cache=True, log_console=True)


In [2]:
def linechart(df):
    m = folium.Map(location=[37.5665, 126.9780], zoom_start=15)
    for _, row in df.iterrows():
        if isinstance(row['geometry'], MultiLineString) and len(row['geometry'].geoms) > 1:
            for line_string in row['geometry'].geoms:
                coordinates = [(lat, lon) for lon, lat in line_string.coords]
                # print(row["유출"])
                line_color = row["Color"]
                folium.PolyLine(locations=coordinates, color=line_color).add_to(m)
        else:
            coordinates = [(lat, lon) for lon, lat in zip(*row['geometry'].xy)]
            line_color = row["Color"]
            folium.PolyLine(locations=coordinates, color=line_color).add_to(m)
    return m

In [8]:
from shapely.geometry import MultiLineString, LineString

link_df=gpd.read_file("../NODELINKDATA\MOCT_LINK.shp",encoding='euc-kr')
link_df['geometry'] = link_df['geometry'].to_crs('EPSG:4326')
temp=link_df['LINK_ID'].apply(lambda x:int(x[:3]))
slink_df=link_df[(temp>=100)&(temp<=124)]
slinkmap = pd.read_csv("LinkMapping.csv")
link_df["LINK_ID"] = link_df["LINK_ID"].apply(int)
slink_df1=pd.merge(left=link_df,right=slinkmap, left_on='LINK_ID', right_on = '표준링크아이디',how='inner')

<>:3: SyntaxWarning: invalid escape sequence '\M'
<>:3: SyntaxWarning: invalid escape sequence '\M'
C:\Users\ilese\AppData\Local\Temp\ipykernel_4460\1378574838.py:3: SyntaxWarning: invalid escape sequence '\M'
  link_df=gpd.read_file("../NODELINKDATA\MOCT_LINK.shp",encoding='euc-kr')


In [9]:
servicelink = pd.read_csv("ServiceLink.csv")
vals = []
prev_node = ""
prev_cnt = 0
start_node = ""
next_node = ""
for i in range(len(servicelink)):
    if prev_node != servicelink.loc[i, "도로명"]:
        prev_node = servicelink.loc[i, "도로명"]
        prev_cnt = 0
    elif start_node == servicelink.loc[i, "시작노드명"]:
        prev_cnt = 1
    start_node = servicelink.loc[i, "시작노드명"]
    next_node = servicelink.loc[i, "종료노드명"]
    vals.append(prev_cnt)
servicelink["유출"] = vals
slink_df_fin = pd.merge(left=slink_df1,right=servicelink, left_on='서비스링크', right_on = '서비스링크',how='inner')
slink_fin = slink_df_fin[["LINK_ID", "LANES", "geometry", "서비스링크", "도로명", "시작노드명", "종료노드명", "유출"]]

In [11]:
pred_list = np.load("pred_list_test.npy")
data = pd.read_csv(f"../Seoul_2024/Seoul01.csv")
road_list = data['지점명'].unique()
pred_list = pred_list[:,0]

pred_data = np.array([[x, y] for x,y in zip(road_list, pred_list)])

pred_data = np.array([[x, y] for x,y in zip(road_list, pred_list)])
pred_data = pd.DataFrame(pred_data, columns=["Road", "Predicted Value"])
pred_data["Road_Fin"] = pred_data["Road"].map(lambda x: x.split('(')[0])
pred_data["Predicted Value"] = pred_data["Predicted Value"].map(lambda x: 0 if float(x)<0 else (8000 if float(x)>8000 else float(x)))
data_fin = pd.merge(left=slink_fin,right=pred_data, left_on='도로명', right_on = 'Road_Fin',how='inner')

In [12]:
def to_color(a):
    if a<1000:
        return 'blue'
    elif 1000<=a<2000:
        return 'green'
    elif 2000<=a<3000:
        return 'yellow'
    else:
        return 'red'

data_fin["Color"] = data_fin["Predicted Value"].map(to_color)

In [13]:
linechart(data_fin)